## Проект Выбор локации для скважины добывающей компании «ГлавРосГосНефть»


In [110]:
import pandas as pd
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LinearRegression
import plotly.express as px
from matplotlib import pyplot as plt
import seaborn as sns
import numpy as np
#from datetime import datetime as dt    
#from scipy import stats as st
%matplotlib inline
#from sklearn.model_selection import cross_val_score
#from  sklearn.tree import DecisionTreeClassifier
#from sklearn.linear_model import LogisticRegression
#from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
#from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_curve, roc_auc_score, precision_recall_curve
from sklearn.model_selection import train_test_split
#from sklearn.preprocessing import StandardScaler
#from sklearn.model_selection import GridSearchCV
#from sklearn.utils import shuffle
#from numpy import argmax
#from sklearn.svm import SVC
from numpy.random import RandomState

In [ ]:
try:
    from pandas_profiling import ProfileReport
except:
    pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip

### Загрузим данные и проведем предобработку

In [111]:
# загрузим данные
try:
    first = pd.read_csv('/Users/ulia/Downloads/geo_data_0.csv')
    second = pd.read_csv('/Users/ulia/Downloads/geo_data_1.csv')
    third = pd.read_csv('/Users/ulia/Downloads/geo_data_2.csv')
except:
    first = pd.read_csv('/datasets/geo_data_0.csv')
    second = pd.read_csv('/datasets/geo_data_1.csv')
    third = pd.read_csv('/datasets/geo_data_2.csv')

In [112]:
ProfileReport(first)

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  1.23it/s]


In [24]:
ProfileReport(second)


Render HTML: 100%|██████████| 1/1 [00:00<00:00,  1.41it/s]


In [25]:
ProfileReport(third)

Render HTML: 100%|██████████| 1/1 [00:01<00:00,  1.10s/it]


В данных отсутствуют пропуски и дубликаты, не все признаки распределены нормально, присутствуют выбросы, но что означают f0,f1,f2 неизвестно, анализ затруднен - оставим данные как есть

### Рассчитаем средние прогнозируемые запасы сырья в скважиах каждого месторождения

In [8]:
def model(df):
    features = df.drop(['product','id'],axis=1)
    target = df[['product']]
    
    features_train, features_vaild, target_train, target_valid = train_test_split(features, target, test_size=0.25, random_state=123)
    mod = LinearRegression()
    mod.fit(features_train, target_train)
    predicted_valid = mod.predict(features_vaild)
    rmse = mean_squared_error(target_valid,predicted_valid)**0.5
    print('Cредний запас сырья составляет {:.3f} тыс баррелей, rmse {:.3f}'.format(predicted_valid.mean(),rmse))
    return predicted_valid, target_valid


In [9]:
predicted_first, target_first = model(first)


Cредний запас сырья составляет 92.549 тыс баррелей, rmse 37.648


In [10]:
predicted_second,target_second = model(second)

Cредний запас сырья составляет 69.280 тыс баррелей, rmse 0.895


In [11]:
predicted_third ,target_third = model(third)

Cредний запас сырья составляет 95.099 тыс баррелей, rmse 40.128


Выводы, первое и 3 месторождения имеют сходные прогнозируемые запасы нефти, ошбика тажке очень похожа, прогнозируемые запасы 2-го месторождения значительно ниже, но и ошибка практически отуствует, таким образом можно сказать, что модель для второго месторождения самая точная


### Рассчитаем достаточный объем сырья для безубыточной разработки каждой скважины

In [12]:
budget = 10**10
wells_in_use = 200
price = 4.5*10**5
print('Минимальный объем сырья для безубыточной разработки 1 скважины', round(budget/wells_in_use/price,2))


Минимальный объем сырья для безубыточной разработки 1 скважины 111.11


Минимальный необходимый объем добычи сырья превышает все наши прогнозируемые средние запасы в каждом месторождении, особенно тревожно, что средние запасы во втором месторождении почти вдвое ниже необходимого, а это наша самая лучшая по качеству предсказаний модель

### Напишем функцию для расчета прибыли

In [16]:
predicted_first = pd.Series(*predicted_first.reshape(1,-1))
predicted_second = pd.Series(*predicted_second.reshape(1,-1))
predicted_third = pd.Series(*predicted_third.reshape(1,-1))


In [17]:
target_first = pd.Series(target_first['product']).reset_index(drop=True)
target_second = pd.Series(target_second['product']).reset_index(drop=True)
target_third = pd.Series(target_third['product']).reset_index(drop=True)

In [107]:
def profit(predictions, target):
    selected_predictions = predictions.sort_values(ascending=False)
    selected_target = target[selected_predictions.index][:200]
    return (selected_target.sum()*price - budget)/10**6



### Расчитаем риски и прибыль для каждого региона 

In [96]:
state = RandomState(123)
def predict_revenue(target, predictions):
    values = []
    count=0
    for i in range(1000):
        target_sampled = target.sample(random_state=state,  frac = 500/len(target) ,replace=True)
        pred_sampled = predictions[target_sampled.index]
        res = profit(pred_sampled, target_sampled)
        values.append(res)
    values = pd.Series(values)
    for value in values:
        if value < 0:
            count +=1
    negative_prob = count/1000
    lower = values.quantile(0.025)
    upper = values.quantile(0.975)
    return values.mean(), negative_prob, lower, upper



In [97]:
mean_first, neg_prob_first, lower_first, upper_first  = predict_revenue(target_first,predicted_first)

#### Первый регион

In [99]:
print('Средняя прибыль составляет {:.2f} млн рублей, доверительный интервал ({:.2f},{:.2f}), риск убытков {:.2%}'.format(mean_first, lower_first, upper_first, neg_prob_first))

Средняя прибыль составляет 504.78 млн рублей, доверительный интервал (-51.83,1029.93), риск убытков 4.00%


#### Второй регион

In [100]:
mean_second, neg_prob_second, lower_second, upper_second  = predict_revenue(target_second,predicted_second)

In [101]:
print('Средняя прибыль составляет {:.2f} млн рублей, доверительный интервал ({:.2f},{:.2f}), риск убытков {:.2%}'.format(mean_second, lower_second, upper_second, neg_prob_second))

Средняя прибыль составляет 525.92 млн рублей, доверительный интервал (100.01,945.01), риск убытков 0.90%


#### Третий регион

In [102]:
mean_third, neg_prob_third, lower_third, upper_third  = predict_revenue(target_third,predicted_third)


In [103]:
print('Средняя прибыль составляет {:.2f} млн рублей, доверительный интервал ({:.2f},{:.2f}), риск убытков {:.2%}'.format(mean_third, lower_third, upper_third, neg_prob_third))

Средняя прибыль составляет 386.98 млн рублей, доверительный интервал (-174.25,933.80), риск убытков 7.70%


## Выводы
По итогам анализа рисков и объемов возможной прибыли, лучшие показатели демонстрирует второй регион (регион 1), средняя прогнозируемая прибыль составляет 525.92 млн рублей, риск убытков менее 1% (соотвветсвует ограничениям на риски), кроме того, модель для этого региона была самой лучшей (с минимальной среднеквадратической ошибкой)

**Рекомендуется к разработке 2 регион**